# Your first scraper
In this project, we will guide you step by step through the process of:

1. creating a self-contained development environment.
1. retrieving some information from an API (a website for computers)
2. leveraging it to scrape a website that does not provide an API
3. saving the output for later processing

Here we query an API for a list of countries and their past leaders. We then extract and sanitize their short bio from Wikipedia. Finally, we save the data to disk.

This task is often the first (coding) step of a datascience project and you will often come back to it in the future.

You will study topics such as *scraping*, *data structures*, *regular expressions*, *concurrency* and *file handling*. We will point out useful resources at the appropriate time. 

Let's dive in!

## 0. Creating a clean environment

Use the [`venv`](https://docs.python.org/3/library/venv.html) command to create a new environment called `wikipedia_scraper_env`.

Activate it and add it to you `.gitignore` file. 

You will find more info about virtual environments in the course content and on the web.

## 1. API Scraping

### 1a. A simple API query
You will start with the basics: how to do a simple request to an [API endpoint](../../2.python/2.python_advanced/05.Scraping/5.apis.ipynb).

You will use the [requests](https://requests.readthedocs.io/en/latest/) external library through the `import` keyword. NOTE: external libraries need to be installed first. Check the [request Quickstart](https://requests.readthedocs.io/en/latest/user/quickstart/) section of the documentation to:

1. Use the `get()` method to connect to this endpoint: https://country-leaders.onrender.com/status
2. Check if the `status_code` is equal to 200, which means OK.
    * if OK, `print()` the `text`` of the response.
    * if not, `print()` the `status_code`. 

Here is an explanation of [HTTP status codes](https://en.wikipedia.org/wiki/List_of_HTTP_status_codes).


In [6]:
# import the requests library (1 line)
import requests

# assign the root url (without /status) to the root_url variable for ease of reference (1 line)
root_url = "https://country-leaders.onrender.com"
# assign the /status endpoint to another variable called status_url (1 line)
status_url = "/status"
# query the /status endpoint using the get() method and store it in the req variable (1 line)
req = requests.get(f"{root_url}{status_url}")
# check the status_code using a condition and print appropriate messages (4 lines)

if req.status_code == 200: 
    print(req.text)
else: 
    print(req.status_code)

"Alive"


### 1b. Dealing with JSON

[JSON](https://quickref.me/json) is the preferred format to deal with data over the web. You cannot avoid it so you would better get acquainted.

Connect to another endpoint called `/countries` but this time the API will return data in the JSON format. 


In [7]:
# Set the countries_url variable (1 line)
countries_url = "https://country-leaders.onrender.com"
# query the /countries endpoint using the get() method and store it in the req variable (1 line)
endpoint = "/countries"
req = requests.get(f"{countries_url}{endpoint}")
# Get the JSON content and store it in the countries variable (1 line)
countries = req.json()
# display the request's status code and the countries variable (1 line)

print(req, countries)

<Response [403]> {'message': 'The cookie is missing'}


### 1c. Cookies anyone?

It looks like the access to this API is restricted...
Query the `/cookie` endpoint and extract the appropriate field to access your cookie.

You will need to use this cookie in each of the following API requests.

In [8]:
# Set the cookie_url variable (1 line)
cookie_url = "https://country-leaders.onrender.com"
# Query the enpoint, set the cookies variable and display it (2 lines)
endpoint = "/cookie"
cookie_req = requests.get(f"{cookie_url}{endpoint}")
cookies = cookie_req.cookies

print(cookies)

<RequestsCookieJar[<Cookie user_cookie=c3516058-b205-43b7-a3b1-0ac94541c085 for country-leaders.onrender.com/>]>


Try to query the countries endpoint using the cookie, save the output and print it.

In [9]:
# query the /countries endpoint, assign the output to the countries variable (1 line)
countries = requests.get(f"{root_url}/countries", cookies=cookies).json()

# display the countries variable (1 line)
print(countries)


['us', 'ma', 'be', 'ru', 'fr']


Chances are the cookie has expired... Thanksfully, you got a nice error message. For now, simply execute the last 2 cells quickly so you get a result.

### 1d. Getting the actual data from the API

Query the `/leaders` endpoint.

In [10]:
# Set the leaders_url variable (1 line)
leaders_url = "https://country-leaders.onrender.com"
# query the /leaders endpoint, assign the output to the leaders variable (1 line)
endpoint = "/leaders"
leaders_req = requests.get(f"{leaders_url}{endpoint}", cookies=cookies)
leaders = leaders_req.json()
# display the leaders variable (1 line)
print(leaders)

{'message': 'Please specify a country'}


It looks like this endpoint requires additional information in order to return its result. Check the API [*documentation*](https://country-leaders.onrender.com/docs) in your web browser.

Change the query to accept *parameters*. You should know where to find help by now.

In [11]:
# query the /leaders endpoint using cookies and parameters (take any country in countries)
# assign the output to the leaders variable (1 line)
leaders = requests.get(f"{root_url}/leaders", cookies=cookies, params={"country": countries[2]}).json()
# display the leaders variable (1 line)
print(leaders)


[{'id': 'Q12978', 'first_name': 'Guy', 'last_name': 'Verhofstadt', 'birth_date': '1953-04-11', 'death_date': None, 'place_of_birth': 'Dendermonde', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Guy_Verhofstadt', 'start_mandate': '1999-07-12', 'end_mandate': '2008-03-20'}, {'id': 'Q12981', 'first_name': 'Yves', 'last_name': 'Leterme', 'birth_date': '1960-10-06', 'death_date': None, 'place_of_birth': 'Wervik', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Yves_Leterme', 'start_mandate': '2009-11-25', 'end_mandate': '2011-12-06'}, {'id': 'Q12983', 'first_name': 'Herman', 'last_name': 'None', 'birth_date': '1947-10-31', 'death_date': None, 'place_of_birth': 'Etterbeek', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Herman_Van_Rompuy', 'start_mandate': '2008-12-30', 'end_mandate': '2009-11-25'}, {'id': 'Q14989', 'first_name': 'Léon', 'last_name': 'Delacroix', 'birth_date': '1867-12-27', 'death_date': '1929-10-15', 'place_of_birth': 'Saint-Josse-ten-Noode', 'wikipedia_url': 'https://nl

### 1e. A sneak peak at the data (finally)

Look inside a few examples. Notice the dictionary keys available for each entry. You have your first example of *structured data*. This data was sanitized for your benefit, meaning it is readily exploitable without modification.

You will also notice there is a Wikipedia link for each entry. You will need to extract additional information there. This will be a case of *semi-structured* data.

The /countries endpoint returns a `list` of several country codes.

You need to loop through this list and query the /leaders endpoint for each one. Save each `json` result in a dictionary called `leaders_per_country`.

In [12]:
# 4 lines

leaders_per_country = {}
for country in countries: 
    response = requests.get(f"{root_url}/leaders", cookies=cookies,params={"country": country})
    leaders_per_country[country] = response.json()

print(leaders_per_country)

{'us': [{'id': 'Q23', 'first_name': 'George', 'last_name': 'Washington', 'birth_date': '1732-02-22', 'death_date': '1799-12-14', 'place_of_birth': 'Westmoreland County', 'wikipedia_url': 'https://en.wikipedia.org/wiki/George_Washington', 'start_mandate': '1789-04-30', 'end_mandate': '1797-03-04'}, {'id': 'Q76', 'first_name': 'Barack', 'last_name': 'Obama', 'birth_date': '1961-08-04', 'death_date': None, 'place_of_birth': 'Kapiolani Medical Center for Women and Children', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Barack_Obama', 'start_mandate': '2009-01-20', 'end_mandate': '2017-01-20'}, {'id': 'Q91', 'first_name': 'Abraham', 'last_name': 'Lincoln', 'birth_date': '1809-02-12', 'death_date': '1865-04-15', 'place_of_birth': 'Sinking Spring Farm', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Abraham_Lincoln', 'start_mandate': '1861-03-04', 'end_mandate': '1865-04-15'}, {'id': 'Q207', 'first_name': 'George', 'last_name': 'Bush', 'birth_date': '1946-07-06', 'death_date': None, 'plac

In [13]:
# or 1 line

leaders_per_country = {country: requests.get(f"{root_url}/leaders", cookies=cookies, params={"country": country}).json() for country in countries}
print(leaders_per_country)


{'us': [{'id': 'Q23', 'first_name': 'George', 'last_name': 'Washington', 'birth_date': '1732-02-22', 'death_date': '1799-12-14', 'place_of_birth': 'Westmoreland County', 'wikipedia_url': 'https://en.wikipedia.org/wiki/George_Washington', 'start_mandate': '1789-04-30', 'end_mandate': '1797-03-04'}, {'id': 'Q76', 'first_name': 'Barack', 'last_name': 'Obama', 'birth_date': '1961-08-04', 'death_date': None, 'place_of_birth': 'Kapiolani Medical Center for Women and Children', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Barack_Obama', 'start_mandate': '2009-01-20', 'end_mandate': '2017-01-20'}, {'id': 'Q91', 'first_name': 'Abraham', 'last_name': 'Lincoln', 'birth_date': '1809-02-12', 'death_date': '1865-04-15', 'place_of_birth': 'Sinking Spring Farm', 'wikipedia_url': 'https://en.wikipedia.org/wiki/Abraham_Lincoln', 'start_mandate': '1861-03-04', 'end_mandate': '1865-04-15'}, {'id': 'Q207', 'first_name': 'George', 'last_name': 'Bush', 'birth_date': '1946-07-06', 'death_date': None, 'plac

It is finally time to create a `get_leaders()` function for the above code. You will build on it later-on. This function takes no parameter. Inside it, you will need to:
1. define the urls
2. get the cookies
2. get the countries
3. loop over them and save their leaders in a dictionary
4. return the dictionary

In [14]:
# < 15 lines
def get_leaders(): 

    #define URL
    root_url = "https://country-leaders.onrender.com"

    # Get the cookies
    cookie_req = requests.get(f"{root_url}/cookie")
    cookies = cookie_req.cookies # extracts the cookies sent by the server

    # Get the countries
    countries_req = requests.get(f"{root_url}/countries", cookies=cookies)
    countries = countries_req.json()

    # Loop over them and save their leaders in a dictionary

    leaders_per_country = {}

    for country in countries: 
        response = requests.get(f"{root_url}/leaders", cookies=cookies, params={"country": country})
        leaders_per_country = response.json()
    return leaders_per_country

Test your function, save the result in the `leaders_per_country` dictionary and check its ouput.

In [15]:
# 2 lines
leaders_per_country = {}
get_leaders()

[{'id': 'Q157',
  'first_name': 'François',
  'last_name': 'Hollande',
  'birth_date': '1954-08-12',
  'death_date': None,
  'place_of_birth': 'Rouen',
  'wikipedia_url': 'https://fr.wikipedia.org/wiki/Fran%C3%A7ois_Hollande',
  'start_mandate': '2012-05-15',
  'end_mandate': '2017-05-14'},
 {'id': 'Q329',
  'first_name': 'Nicolas',
  'last_name': 'Sarkozy',
  'birth_date': '1955-01-28',
  'death_date': None,
  'place_of_birth': 'Paris',
  'wikipedia_url': 'https://fr.wikipedia.org/wiki/Nicolas_Sarkozy',
  'start_mandate': '2007-05-16',
  'end_mandate': '2012-05-15'},
 {'id': 'Q2038',
  'first_name': 'François',
  'last_name': 'Mitterrand',
  'birth_date': '1916-10-26',
  'death_date': '1996-01-08',
  'place_of_birth': 'Jarnac',
  'wikipedia_url': 'https://fr.wikipedia.org/wiki/Fran%C3%A7ois_Mitterrand',
  'start_mandate': '1981-05-21',
  'end_mandate': '1995-05-17'},
 {'id': 'Q2042',
  'first_name': 'Charles',
  'last_name': 'de Gaulle',
  'birth_date': '1890-11-22',
  'death_date': '

## 2. Extracting data from Wikipedia

Query one of the leaders' Wikipedia urls and display its `text` (not JSON).

In [16]:
# 3 lines
headers = {
    "User-Agent": "SeanBot/1.0 (sean@example.com) Python scraping for learning"
}

r = requests.get(f"https://fr.wikipedia.org/wiki/Emmanuel_Macron", headers=headers)
text = r.text

print(text)

<!DOCTYPE html>
<html class="client-nojs vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-content-enabled vector-feature-custom-font-size-clientpref-1 vector-feature-appearance-pinned-clientpref-1 skin-theme-clientpref-day vector-sticky-header-enabled vector-toc-available" lang="fr" dir="ltr">
<head>
<meta charset="UTF-8">
<title>Emmanuel Macron — Wikipédia</title>
<script>(function(){var className="client-js vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-content-enabled vector-feature-custom-font-size-clientpref-1

Ouch! You get the raw HTML code of the webpage. If you try to deal with it without tools, you will be there all night. Instead, use the [beautiful soup 4](https://www.crummy.com/software/BeautifulSoup/bs4/doc/) *external* library. You will find more info about it [here](../../2.python/2.python_advanced/05.Scraping/1.beautifulsoup_basic.ipynb) and [here](../../2.python/2.python_advanced/05.Scraping/2.beautifulsoup_advanced.ipynb)

Using the Quickstart section, start by importing the library and loading the output of your `get_text()` function.

Use the `prettify()` function and print it to take a look. You will start the actual parsing in the next step.

In [17]:
# 3 lines
from bs4 import BeautifulSoup
soup = BeautifulSoup(text, "html.parser")
print(soup.prettify()) 



<!DOCTYPE html>
<html class="client-nojs vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-content-enabled vector-feature-custom-font-size-clientpref-1 vector-feature-appearance-pinned-clientpref-1 skin-theme-clientpref-day vector-sticky-header-enabled vector-toc-available" dir="ltr" lang="fr">
 <head>
  <meta charset="utf-8"/>
  <title>
   Emmanuel Macron — Wikipédia
  </title>
  <script>
   (function(){var className="client-js vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-content-enabled vector-feature-custom-fon

That looks better but you need to extract the right part of the webpage: the text of the first paragraph.

It is a bit tricky because Wikipedia pages slightly differ in structure from one language to the next. We cannot simply get the text for the first HTML paragraph.

You will start by getting all the HTML paragraphs from the HTML source and saving them in the `paragraphs` variable.

Use the documentation or google the appropriate keywords.

In [29]:
# 2 lines
paragraphs = soup.find_all("p")

for p in paragraphs[:5]: 
    print(p.get_text())



Pour les articles homonymes, voir Macron.



Emmanuel Macron ([ɛmanɥɛl makʁɔ̃][e] Écouterⓘ), né le 21 décembre 1977 à Amiens (Somme), est un haut fonctionnaire, banquier d'affaires et homme d'État français. Il est président de la République française depuis le 14 mai 2017.

Sorti de l'École nationale d'administration (ENA) en 2004, il devient inspecteur des finances. En 2007, il est nommé rapporteur adjoint de la commission pour la libération de la croissance française (« commission Attali »). L'année suivante, il rejoint la banque d'affaires Rothschild & Cie, dont il devient associé-gérant en 2010.



If you try different urls, you might find that the paragraph you want may be at a different index each time.

That is where you need to be clever and ask yourself what would be a reliable way to identify the right index ie. which string matches only the first paragraph whatever the language...

Spend a good 30 minutes on the problem and brainstorm with your fellow learners. If you come out empty handed, ask your coach.

1. Loop over the HTML paragraphs
2. When you have identified the correct one:
   * Store the [text](https://www.crummy.com/software/BeautifulSoup/bs4/doc/#output) inside the `first_paragraph` variable
   * Exit the loop

In [19]:
# <10 lines
first_paragraph = []
    
for p in paragraphs: 
    text = p.get_text(strip=True)
    if text and p.find("b"): 
        first_paragraph = text
        break

print(first_paragraph)

Emmanuel Macron([ɛmanɥɛlmakʁɔ̃][e]Écouterⓘ), né le21 décembre 1977àAmiens(Somme), est unhaut fonctionnaire,banquier d'affairesethomme d'Étatfrançais. Il estprésident de la République françaisedepuis le14 mai 2017.


At this stage, you can create a function to maintain consistency in your code. We will give you its *skeleton*, you will copy the code you wrote and make it work inside a function.

Don't forget to test your function.

In [30]:
# 10 lines
def get_first_paragraph(wikipedia_url):
    print(wikipedia_url) # keep this for the rest of the notebook
    
    headers = {
        "User-Agent": "SeanBot/1.0 (learning scraping)"
    }

    response = requests.get(wikipedia_url, headers=headers)
    soup = BeautifulSoup(response.text, "html.parser")

    paragraphs = soup.find_all("p")

    first_paragraph = ""

    for p in paragraphs: 
        text = p.get_text(strip=True)
        if text and p.find("b"): 
            first_paragraph = text
    return first_paragraph

In [31]:
# Test: 3 lines
print(get_first_paragraph("https://fr.wikipedia.org/wiki/Emmanuel_Macron"))


https://fr.wikipedia.org/wiki/Emmanuel_Macron
Emmanuel Macron([ɛmanɥɛlmakʁɔ̃][e]Écouterⓘ), né le21 décembre 1977àAmiens(Somme), est unhaut fonctionnaire,banquier d'affairesethomme d'Étatfrançais. Il estprésident de la République françaisedepuis le14 mai 2017.


### 2a. Regular expressions to the rescue

Now that you have extracted the content of the first paragraph, the only thing that remains to finish your Wikipedia scraper is to sanitize the output.

Indeed some Wikipedia references, HTML code, phonetic pronunciation etc. may linger. You might find *regular expressions* handy to get rid of them and obtain pristine text. You will find some useful documentation about regular expressions [here](../../2.python/2.python_advanced/03.Regex/regex.ipynb)

Once you have one of your regex working online, try it in the cell below. 

Hints: 
* Check the `sub()` method documentation.
* Make sure to test urls in different languages. Some may look good but other do not.

In [22]:
# 3 lines
import re

first_paragraph = re.sub(r"\[.*?\]", "", first_paragraph)
first_paragraph = re.sub(r"\(.*?\)", "", first_paragraph)
first_paragraph = re.sub(r"\s+", " ", first_paragraph).strip()

print(first_paragraph)


Emmanuel Macron, né le21 décembre 1977àAmiens, est unhaut fonctionnaire,banquier d'affairesethomme d'Étatfrançais. Il estprésident de la République françaisedepuis le14 mai 2017.


Overwrite the `get_first_paragraph()` function by applying your regex to the first paragraph before returning it.

In [23]:
# 10 lines

def get_first_paragraph(wikipedia_url):
    print(wikipedia_url) # keep this for the rest of the notebook
    
    headers = {
        "User-Agent": "SeanBot/1.0 (learning scraping)"
    }

    response = requests.get(wikipedia_url, headers=headers)
    soup = BeautifulSoup(response.text, "html.parser")

    paragraphs = soup.find_all("p")

    first_paragraph = ""

    for p in paragraphs: 
        text = p.get_text(strip=True)
        if text and p.find("b"): 
            first_paragraph = text
            break

    first_paragraph = re.sub(r"\[.*?\]", "", first_paragraph)
    first_paragraph = re.sub(r"\(.*?\)", "", first_paragraph)
    first_paragraph = re.sub(r"\s+", " ", first_paragraph).strip()

    return first_paragraph

print(get_first_paragraph("https://fr.wikipedia.org/wiki/Emmanuel_Macron"))


https://fr.wikipedia.org/wiki/Emmanuel_Macron
Emmanuel Macron, né le21 décembre 1977àAmiens, est unhaut fonctionnaire,banquier d'affairesethomme d'Étatfrançais. Il estprésident de la République françaisedepuis le14 mai 2017.


Come up with other regexes to capture other patterns and sanitize the outputs completely. Modify your `get_first_paragraph()` function accordingly.

In [24]:
session = requests.Session()
session.headers.update({"User-Agent": "SeanBot/1.0 (learning scraping)"})
WIKI_CACHE = {}

def get_first_paragraph(wikipedia_url):
    if wikipedia_url in WIKI_CACHE:
        return WIKI_CACHE[wikipedia_url]

    r = session.get(wikipedia_url, timeout=10)
    soup = BeautifulSoup(r.text, "html.parser")

    first_paragraph = ""
    for p in soup.find_all("p"):
        text = p.get_text(" ", strip=True)
        if text and p.find("b"):
            first_paragraph = text
            break

    for pat, rep in [
        (r"\[[^\]]*?\]", ""), (r"\([^)]*?\)", ""), (r"/[^/]{2,}/", ""),
        (r"(?i)\b(écouter|listen)\b", ""), (r"\u00a0", " "),
        (r"\s+([,;:.!?])", r"\1"), (r"\s+", " ")
    ]:
        first_paragraph = re.sub(pat, rep, first_paragraph).strip()

    WIKI_CACHE[wikipedia_url] = first_paragraph
    return first_paragraph


## 3. Putting it all together

Let's go back to your `get_leaders()` function and update it with an *inner* loop over each leader. You will query the url provided and extract the first paragraph using the `get_first_paragraph()` function you just finished. You will then update that `leader`'s dictionary and move on to the next one.

Notice, the rest of the code should not change since you modify the leader's data one by one.

In [25]:
def get_leaders():
    root_url = "https://country-leaders.onrender.com"

    cookies = session.get(f"{root_url}/cookie", timeout=10).cookies
    countries = session.get(f"{root_url}/countries", cookies=cookies, timeout=10).json()

    leaders_per_country = {}

    for country in countries:
        leaders = session.get(f"{root_url}/leaders", cookies=cookies, params={"country": country}, timeout=10).json()
        
        for leader in leaders:
            url = leader.get("wikipedia_url")
            
            if url:
                leader["first_paragraph"] = get_first_paragraph(url)
        leaders_per_country[country] = leaders

    return leaders_per_country

In [26]:
# Check the output of your function (2 lines)

data = get_leaders()
data

KeyboardInterrupt: 

Does the function crash in the middle of the loop? Chances are the cookies have expired while looping over the leaders.

Modify your function with an *exception* or check if the `status_code` is a cookie error. In either case, get new cookies and query the api again.

If your code did not crash,

In [ ]:
# < 25 lines

session = requests.Session()
session.headers.update({"User-Agent": "SeanBot/1.0 (learning scraping)"})
WIKI_CACHE = {}

def get_first_paragraph(wikipedia_url):
    if wikipedia_url in WIKI_CACHE:
        return WIKI_CACHE[wikipedia_url]

    r = session.get(wikipedia_url, timeout=10)
    soup = BeautifulSoup(r.text, "html.parser")

    first_paragraph = ""
    for p in soup.find_all("p"):
        text = p.get_text(" ", strip=True)
        if text and p.find("b"):
            first_paragraph = text
            break

    for pat, rep in [
        (r"\[[^\]]*?\]", ""), (r"\([^)]*?\)", ""), (r"/[^/]{2,}/", ""),
        (r"(?i)\b(écouter|listen)\b", ""), (r"\u00a0", " "),
        (r"\s+([,;:.!?])", r"\1"), (r"\s+", " ")
    ]:
        first_paragraph = re.sub(pat, rep, first_paragraph).strip()

    WIKI_CACHE[wikipedia_url] = first_paragraph
    return first_paragraph


def get_leaders():
    root_url = "https://country-leaders.onrender.com"

    cookies = session.get(f"{root_url}/cookie", timeout=10).cookies
    countries_resp = session.get(f"{root_url}/countries", cookies=cookies, timeout=10)

    if countries_resp.status_code != 200: 
        cookies = session.get(f"{root_url}/cookie", timeout=10).cookies
        countries_resp = session.get(f"{root_url}/countries", cookies=cookies, timeout=10)
    
    countries = countries_resp.json()
    leaders_per_country = {}

    for country in countries:
        leaders_resp = session.get(f"{root_url}/leaders", cookies=cookies, params={"country": country}, timeout=10)
        
        if leaders_resp.status_code != 200:
            cookies = session.get(f"{root_url}/cookie", timeout=10).cookies
            leaders_resp = session.get(f"{root_url}/leaders", cookies=cookies, params={"country": country}, timeout=10)
        
        leaders = leaders_resp.json()
        
        for leader in leaders:
            url = leader.get("wikipedia_url")
            
            if url:
                leader["first_paragraph"] = get_first_paragraph(url)
        leaders_per_country[country] = leaders

    return leaders_per_country



Check the output of your function again.

In [ ]:
# Check the output of your function (1 line)

data = get_leaders()
data

{'be': [{'id': 'Q12978',
   'first_name': 'Guy',
   'last_name': 'Verhofstadt',
   'birth_date': '1953-04-11',
   'death_date': None,
   'place_of_birth': 'Dendermonde',
   'wikipedia_url': 'https://nl.wikipedia.org/wiki/Guy_Verhofstadt',
   'start_mandate': '1999-07-12',
   'end_mandate': '2008-03-20',
   'first_paragraph': 'Guy Maurice Marie-Louise Verhofstadt is een Belgisch politicus voor de Open Vlaamse Liberalen en Democraten. Hij was premier van België van 12 juli 1999 tot 20 maart 2008 in drie regeringen. Hij beëindigde zijn actieve politieke carrière in het Europees Parlement, waar hij van 2009 tot 2019 fractieleider van de Alliantie van Liberalen en Democraten voor Europa was.'},
  {'id': 'Q12981',
   'first_name': 'Yves',
   'last_name': 'Leterme',
   'birth_date': '1960-10-06',
   'death_date': None,
   'place_of_birth': 'Wervik',
   'wikipedia_url': 'https://nl.wikipedia.org/wiki/Yves_Leterme',
   'start_mandate': '2009-11-25',
   'end_mandate': '2011-12-06',
   'first_par

Well done! It took a while however... Let's speed things up. The main *bottleneck* is the loop. We call on the Wikipedia website many times.

You will use the same *session* to call all the wikipedia pages. Check the *Advanced Usage* section of the Requests module's documentation.

Start by modifying the `get_first_paragraph()` function to accept a session parameter and adjust the `get()` method call.

In [ ]:
# < 20 lines
# < 25 lines

session = requests.Session()
session.headers.update({"User-Agent": "SeanBot/1.0 (learning scraping)"})
WIKI_CACHE = {}

def get_first_paragraph(wikipedia_url, session):
    if wikipedia_url in WIKI_CACHE:
        return WIKI_CACHE[wikipedia_url]

    r = session.get(wikipedia_url, timeout=10)
    soup = BeautifulSoup(r.text, "html.parser")

    first_paragraph = ""
    for p in soup.find_all("p"):
        text = p.get_text(" ", strip=True)
        if text and p.find("b"):
            first_paragraph = text
            break

    for pat, rep in [
        (r"\[[^\]]*?\]", ""), (r"\([^)]*?\)", ""), (r"/[^/]{2,}/", ""),
        (r"(?i)\b(écouter|listen)\b", ""), (r"\u00a0", " "),
        (r"\s+([,;:.!?])", r"\1"), (r"\s+", " ")
    ]:
        first_paragraph = re.sub(pat, rep, first_paragraph).strip()

    WIKI_CACHE[wikipedia_url] = first_paragraph
    return first_paragraph


def get_leaders():
    root_url = "https://country-leaders.onrender.com"

    cookies = session.get(f"{root_url}/cookie", timeout=10).cookies
    countries_resp = session.get(f"{root_url}/countries", cookies=cookies, timeout=10)

    if countries_resp.status_code != 200: 
        cookies = session.get(f"{root_url}/cookie", timeout=10).cookies
        countries_resp = session.get(f"{root_url}/countries", cookies=cookies, timeout=10)
    
    countries = countries_resp.json()
    leaders_per_country = {}

    for country in countries:
        leaders_resp = session.get(f"{root_url}/leaders", cookies=cookies, params={"country": country}, timeout=10)
        
        if leaders_resp.status_code != 200:
            cookies = session.get(f"{root_url}/cookie", timeout=10).cookies
            leaders_resp = session.get(f"{root_url}/leaders", cookies=cookies, params={"country": country}, timeout=10)
        
        leaders = leaders_resp.json()
        
        for leader in leaders:
            url = leader.get("wikipedia_url")
            
            if url:
                leader["first_paragraph"] = get_first_paragraph(url, session)
        leaders_per_country[country] = leaders

    return leaders_per_country



Modify your `get_leaders()` function to make use of a single session for all the Wikipedia calls.
1. create a `Session` object outside of the loop over countries.
2. pass it to the `get_first_paragraph()` function as an argument.

In [ ]:
# <25 lines
def get_first_paragraph(wikipedia_url, session):
    r = session.get(wikipedia_url, timeout=10)
    soup = BeautifulSoup(r.text, "html.parser")

    first_paragraph = ""
    for p in soup.find_all("p"):
        text = p.get_text(" ", strip=True)
        if text and p.find("b"):
            first_paragraph = text
            break

    for pat, rep in [
        (r"\[[^\]]*?\]", ""), (r"\([^)]*?\)", ""), (r"/[^/]{2,}/", ""),
        (r"(?i)\b(écouter|listen)\b", ""), (r"\u00a0", " "),
        (r"\s+([,;:.!?])", r"\1"), (r"\s+", " ")
    ]:
        first_paragraph = re.sub(pat, rep, first_paragraph).strip()

    return first_paragraph


In [ ]:
def get_leaders():
    root_url = "https://country-leaders.onrender.com"

    session = requests.Session()
    session.headers.update({"User-Agent": "SeanBot/1.0 (learning scraping)"})

    cookies = session.get(f"{root_url}/cookie", timeout=10).cookies
    countries = session.get(f"{root_url}/countries", cookies=cookies, timeout=10).json()

    leaders_per_country = {}

    for country in countries:
        leaders = session.get(f"{root_url}/leaders", cookies=cookies, params={"country": country}, timeout=10).json()

        if not isinstance(leaders, list):  # cookie expired / error payload
            cookies = session.get(f"{root_url}/cookie", timeout=10).cookies
            leaders = session.get(f"{root_url}/leaders", cookies=cookies, params={"country": country}, timeout=10).json()
            
        for leader in leaders:
            url = leader.get("wikipedia_url")
            if url:
                leader["first_paragraph"] = get_first_paragraph(url, session)

        leaders_per_country[country] = leaders

    return leaders_per_country


Test your new functions.



In [ ]:
data = get_leaders()
data

{'be': [{'id': 'Q12978',
   'first_name': 'Guy',
   'last_name': 'Verhofstadt',
   'birth_date': '1953-04-11',
   'death_date': None,
   'place_of_birth': 'Dendermonde',
   'wikipedia_url': 'https://nl.wikipedia.org/wiki/Guy_Verhofstadt',
   'start_mandate': '1999-07-12',
   'end_mandate': '2008-03-20',
   'first_paragraph': 'Guy Maurice Marie-Louise Verhofstadt is een Belgisch politicus voor de Open Vlaamse Liberalen en Democraten. Hij was premier van België van 12 juli 1999 tot 20 maart 2008 in drie regeringen. Hij beëindigde zijn actieve politieke carrière in het Europees Parlement, waar hij van 2009 tot 2019 fractieleider van de Alliantie van Liberalen en Democraten voor Europa was.'},
  {'id': 'Q12981',
   'first_name': 'Yves',
   'last_name': 'Leterme',
   'birth_date': '1960-10-06',
   'death_date': None,
   'place_of_birth': 'Wervik',
   'wikipedia_url': 'https://nl.wikipedia.org/wiki/Yves_Leterme',
   'start_mandate': '2009-11-25',
   'end_mandate': '2011-12-06',
   'first_par

## 4. Saving your hard work

The final step is to save the ``leaders_per_country`` dictionary in the `leaders.json` file using the [json](https://docs.python.org/3/library/json.html) module. Check out the `with` statement.

In [ ]:
# 3 lines
import json 

data = get_leaders()

with open("leaders.json", "w", encoding="utf-8") as f: 
    json.dump(data, f, indent=4, ensure_ascii=False)

Make sure the file can be read back. Write the code to read the file. And check the variables are the same.

In [ ]:
# 3 lines
with open("leaders.json", "r", encoding="utf-8") as f:
    loaded_data = json.load(f)

print(data == loaded_data)

True


Make a function `save(leaders_per_country)` to call this code easily.

In [ ]:
# 3 lines
def save(leaders_per_country, filename="leaders.json"): 
    with open(filename, "w", encoding="utf-8") as f: 
        json.dump(leaders_per_country, f, indent=4, ensure_ascii=False)

In [ ]:
# Call the function (1 line)
data = get_leaders()
save(data)


## 5. Tidy things up in a stand-alone python script

Congratulations! You now have a working scraper! However, your code is scattered throughout this notebook along side the tutorials. Hardly production ready...

Copy and paste what you need in a separate `leaders_scraper.py` file.
Make sure it works by calling `python3 leaders_scraper.py`

## (Optional) To go further

If you want to practice scraping, you can read this section and tackle the exercises.

1. Restructure your code by using OOP (see ReadMe).
2. You have noticed the API returns very partial results for country leaders. Many are missing. Overwrite the `get_leaders()` function to get its list from Wikipedia and extract their *personal details* from the frame on the side.

Good luck!